## Mistral-7B-Instruct
Sources:

- https://mistral.ai/news/announcing-mistral-7b/
- https://huggingface.co/mistralai/Mistral-7B-Instruct-v0.1
- https://huggingface.co/TheBloke/Mistral-7B-Instruct-v0.1-GGUF
- https://huggingface.co/spaces/osanseviero/mistral-super-fast/blob/main/Mistral_7B.ipynb

### Setup

In [ ]:
%pip install -U openai

In [ ]:
%pip show openai

In [46]:
import openai
import os

openai.api_key  = os.getenv('HF_API_KEY')
openai.api_base = "https://limcheekin-mistral-7b-instruct-v0-1-gguf.hf.space/v1"


### Prompt Format
Sources: 
- https://colab.research.google.com/drive/1F2PeWl5FOHv4sjd7XTEu40JjqbFhC3LB?usp=sharing
- https://huggingface.co/spaces/osanseviero/mistral-super-fast/blob/main/Mistral_7B.ipynb

```
<s>[INST] <user_prompt> [/INST]
<assistant_response> </s>
[INST] <user_prompt>[/INST]
```
---
```
<s>[INST] {{ user_msg_1 }} [/INST] {{ model_answer_1 }}</s> [INST] {{ user_msg_2 }} [/INST] {{ model_answer_2 }}</s>
```

In [47]:
def get_prompt(system_prompt: str, instruction: str):
    prompt = f"<s>[INST]System: {system_prompt}[/INST]</s> [INST]User: {instruction}[/INST]"
    return prompt

### Completion Function

In [48]:
import time

DEFAULT_SYSTEM_PROMPT = "You are a helpful assistant, you will complete the task by follow the instructions given."

# Source: https://platform.openai.com/docs/api-reference/chat/create
def get_completion(prompt, system_prompt=DEFAULT_SYSTEM_PROMPT, temperature=0.0, max_tokens=512):
    messages = [{"role": "user", "content": get_prompt(system_prompt=system_prompt, instruction=prompt)}]
    start_time = time.time()
    response = openai.ChatCompletion.create(
        model="",
        messages=messages,
        temperature=temperature, 
        max_tokens=max_tokens,
        request_timeout=600,
        stream=True
    )
    return combine_chunks(start_time, response)

# Source: https://github.com/openai/openai-cookbook/blob/main/examples/How_to_stream_completions.ipynb
def combine_chunks(start_time, response):
    # create variables to collect the stream of chunks
    collected_messages = []
    # iterate through the stream of events
    for chunk in response:
        chunk_time = time.time() - start_time  # calculate the time delay of the chunk
        chunk_message = chunk['choices'][0]['delta']  # extract the message
        collected_messages.append(chunk_message)  # save the message
        print(chunk_message.get('content', ''), end='')
        # print(f"Message received {chunk_time:.2f} seconds after request: {chunk_message}")  # print the delay and text

    # print the time delay and text received
    print(f"\nResponse time taken: {chunk_time:.2f}s")
    full_reply_content = ''.join([m.get('content', '') for m in collected_messages])
    return full_reply_content    

In [49]:
text = "What is AI?"
response = get_completion(text)

1. AI stands for Artificial Intelligence. It refers to the development of computer systems that can perform tasks that typically require human intelligence, such as visual perception, speech recognition, decision-making, and language translation.
2. AI technology involves machine learning algorithms, deep learning neural networks, natural language processing (NLP), and other techniques that enable computers to learn from data and improve their performance over time.
3. AI has many applications in various industries, including healthcare, finance, transportation, education, and entertainment. It is used for tasks such as predictive analytics, recommendation systems, chatbots, and autonomous vehicles.
4. AI is a rapidly evolving field with new advancements being made all the time. It has the potential to revolutionize many aspects of our lives and improve our quality of life in various ways.
Response time taken: 44.19s
